<div style="background-color: #a3e4d7 ; padding: 10px; border: 1px solid green;color: solid green">
<h1 align="center"; style="color:#cc0066;">Italian take away in the heart of Amsterdam</h1>
</div>

<h3 align="center"> Capstone Project - The Battle of the Neighborhoods (Week 2)</h3>
<h4 align="center"> Applied Data Science Capstone by IBM/Coursera</h4>

--------------------------------------------------------

## Table of contents
<!--- # <div class="alert alert-block alert-info" style="margin-top: 20px">
-->    
<div style="padding: 10px; border: 1px solid green;color: solid green">
    
1. [Introduction: Business Problem](#introduction)
2. [Data acquisition and cleaning](#data)
3. [Methodology](#methodology)
4. [Analysis](#analysis)
5. [Results and Discussion](#results)
6. [Conclusions](#conclusions)
</div>


<a id="introduction"></a>
## 1. Introduction: Business Problem 

The aim of this project is to find an optimal location for an Italian take away in the heart of Amsterdam. In fact, Italian food is appreciated worldwide and lots of tourists but also locals in their countries use to try Italian specialties even when not in Italy.

The idea of a take away occurred to me while thinking on the way italians do experience lunch compared to other cultures, or rather, a structured lunch with more than one course instead of a rapid lunch with a sandwich or a slice of pizza, that is more typical outside Italy, especially in northern Europe.

This project is thought to meet the real needs of the locals and offer products that are made with 100% imported Italian raw materials at the same time. Thus, this report is mainly targeted to stakeholders who are interested in or want to bet in the opening of a food venue to provide a new type of food service.

Since there are lots of italian restaurants in Amsterdam, the focus will be first on finding a location with a minor concentration of italian food venues. Moreover, proximity to city centre, universities, offices and green areas will be considered as a parameter to define the best location for the take away.

The most promising neighborhoods will be found based on these criteria and using the data science instruments.  Advantages of each area will be finally expressed so that the best possible final location can be chosen by stakeholders.

<a id="data"></a>
## 2. Data acquisition and cleaning

Based on the problem definition, factors that will influence the choice of the best location are:

* number of existing fast food (can be included in the take away category) in the neighborhood
* number of and distance to Italian restaurants in the neighborhood (if any)
* distance of neighborhood from city centre
* distance of neighborhood from universities and offices
* distance of neighborhood from main parks and green areas

A regularly spaced grid of squared locations, centered around city center, will be used to define the neighborhoods.

To extract and generate the required information, the following data sources will be used:
* centres of candidate areas will be generated using algorithms and approximate addresses of these areas centre will be obtained using **geopy**, a Python client for several popular geocoding web services
* the number of restaurants, their type and location in each neighborhood will be obtained using Foursquare API
* the coordinates of Amsterdam centre will be obtained using **geopy** and the address for the geocoding will be set as that of the well-known Dam Square.


#### Candidate Neighborhoods

First thing to do is getting the latitude and longitude coordinates of all possible neighborhoods. This will be achieved by creating a grid of cells covering the area of interest which is 3x3 kilometers centred around Dam Square.

In [1]:
# =============================================================================
# Download & install the required modules
# =============================================================================

!conda install -c conda-forge geopy --yes
!conda install -c conda-forge folium=0.5.0 --yes
!conda install -c conda-forge pandas --yes

import numpy
import pandas as pd
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)
import json
from geopy.geocoders import Nominatim
import requests
from pandas.io.json import json_normalize
import matplotlib.cm as cm
import matplotlib.colors as colors
from sklearn.cluster import KMeans
import folium

print('Libraries imported.')
# =============================================================================

Solving environment: done

## Package Plan ##

  environment location: /home/jupyterlab/conda/envs/python

  added / updated specs:
    - geopy


The following packages will be downloaded:

    package                    |            build
    ---------------------------|-----------------
    geographiclib-1.50         |             py_0          34 KB  conda-forge
    geopy-2.0.0                |     pyh9f0ad1d_0          63 KB  conda-forge
    openssl-1.1.1g             |       h516909a_1         2.1 MB  conda-forge
    ------------------------------------------------------------
                                           Total:         2.2 MB

The following NEW packages will be INSTALLED:

  geographiclib      conda-forge/noarch::geographiclib-1.50-py_0
  geopy              conda-forge/noarch::geopy-2.0.0-pyh9f0ad1d_0

The following packages will be UPDATED:

  openssl                                 1.1.1g-h516909a_0 --> 1.1.1g-h516909a_1



openssl-1.1.1g       | 2.1 MB    | #####

In [2]:
# =============================================================================
# Getting the Dam Square latitude and longitude coordinates using geolocator
# =============================================================================

def get_coordinates(address):
    try:
        geolocator = Nominatim(user_agent="foursquare_agent")
        location = geolocator.geocode(address)
        lat = location.latitude
        lon = location.longitude
        return [lat, lon]
    except:
        return [None, None]

    
address = 'Dam Square, Amsterdam, Netherlands'
ams_center = get_coordinates(address)
print('Coordinate of {}: {}'.format(address, ams_center))

Coordinate of Dam Square, Amsterdam, Netherlands: [52.37324315, 4.892514790930079]


The area of interest is quite small compared to the city limits. In fact, the idea is to find the best location for an Italian take away in the very heart of Amsterdam. Thus, the **neighborhoods** that has to be defined will have a **squared shape with side of 300 metres**.
The **grid** of area candidates will be centred in Dam Square and will **expand till ~1.5km** from it.


In [3]:
from geopy import Point
from geopy.distance import geodesic

distKm = 1.5
print('center:', ams_center[0], ams_center[1])
print('north: ', geodesic(kilometers=distKm).destination(Point(ams_center[0], ams_center[1]), 0).format_decimal())
print('east:  ', geodesic(kilometers=distKm).destination(Point(ams_center[0], ams_center[1]), 90).format_decimal())
print('south: ', geodesic(kilometers=distKm).destination(Point(ams_center[0], ams_center[1]), 180).format_decimal())
print('west:  ', geodesic(kilometers=distKm).destination(Point(ams_center[0], ams_center[1]), 270).format_decimal())

center: 52.37324315 4.892514790930079
north:  52.38672331997083, 4.892514790930079
east:   52.37324109798362, 4.914539484097067
south:  52.359762949101146, 4.892514790930079
west:   52.37324109798362, 4.870490097763091


In [4]:
# BOUNDING BOX COORDINATES

bottomLeft = [float(geodesic(kilometers=distKm).destination(Point(ams_center[0], ams_center[1]), 180).format_decimal().split(',')[0]),float(geodesic(kilometers=distKm).destination(Point(ams_center[0], ams_center[1]), 270).format_decimal().split(',')[1])]
bottomRight = [float(geodesic(kilometers=distKm).destination(Point(ams_center[0], ams_center[1]), 180).format_decimal().split(',')[0]),float(geodesic(kilometers=distKm).destination(Point(ams_center[0], ams_center[1]), 90).format_decimal().split(',')[1])]
topLeft = [float(geodesic(kilometers=distKm).destination(Point(ams_center[0], ams_center[1]), 0).format_decimal().split(',')[0]),float(geodesic(kilometers=distKm).destination(Point(ams_center[0], ams_center[1]), 270).format_decimal().split(',')[1])]
topRight = [float(geodesic(kilometers=distKm).destination(Point(ams_center[0], ams_center[1]), 0).format_decimal().split(',')[0]),float(geodesic(kilometers=distKm).destination(Point(ams_center[0], ams_center[1]), 90).format_decimal().split(',')[1])]
print('Corner Coordinates of the square area around {}: top left corner {} , top right corner {}, bottom left corner {}, bottom right corner {}'.format(address, topLeft, topRight, bottomLeft, bottomRight))

Corner Coordinates of the square area around Dam Square, Amsterdam, Netherlands: top left corner [52.38672331997083, 4.870490097763091] , top right corner [52.38672331997083, 4.914539484097067], bottom left corner [52.359762949101146, 4.870490097763091], bottom right corner [52.359762949101146, 4.914539484097067]


Let's visualize the bounding box for the squared 3x3 km area around Dam Square

In [5]:
map_Ams = folium.Map(location=ams_center, zoom_start=14)
folium.Marker(ams_center, popup='Dam Square').add_to(map_Ams)
folium.features.RectangleMarker(bounds=[topLeft, topRight, bottomLeft, bottomRight], color='#ff7800', fill_color='#ffff00', fill_opacity=0.2).add_to(map_Ams)

map_Ams

In [6]:
nOfDivisions = int(3000/300)

cols = numpy.linspace(bottomLeft[1], bottomRight[1], num=nOfDivisions)
rows = numpy.linspace(bottomLeft[0], topLeft[0], num=nOfDivisions)

print('Number of divisions is {} so the total number of neighborhoods should be: {}'.format(nOfDivisions-1, numpy.power(nOfDivisions-1,2)))

Number of divisions is 9 so the total number of neighborhoods should be: 81


In [7]:
lat, lon = numpy.meshgrid(rows, cols)
#positions = numpy.vstack([lat.ravel(), lon.ravel()])

In [8]:
singleBounds = []
for s1 in range(1,len(lon)):
    for s2 in range(1,len(lon[s1])):
        localBounds = [[lat[s1][s2],lon[s1][s2]],[lat[s1-1][s2],lon[s1-1][s2]],
                       [lat[s1][s2-1],lon[s1-1][s2]],[lat[s1-1][s2-1],lon[s1][s2]]]
        singleBounds.append(localBounds)

# CHECKING THE TOTAL NUMBER OF SQUARES (NEIGHBORHOODS)
print('Total number of squares composing the final grid: {}'.format(len(singleBounds)))

Total number of squares composing the final grid: 81


Let's visualize the grid of squares identifying all possible neighborhoods in the heart of Amsterdam

In [9]:
map_AmsHeart = folium.Map(location=ams_center, zoom_start=14)
folium.Marker(ams_center, popup='Dam Square').add_to(map_AmsHeart)
for innerSquare in range(len(singleBounds)):
    folium.features.RectangleMarker(bounds=singleBounds[innerSquare], color='#a11e06', fill_color='#a11e06', 
                                    fill_opacity=0.2).add_to(map_AmsHeart)

map_AmsHeart

Getting the latitude and longitude coordinates of each squared neighborhood centre and displaying it on the map

In [10]:
import math
centres = []
distances = []
def getCentreLatLong(squareCorners):
    lat = 0.5*squareCorners[0][0] + 0.5*squareCorners[3][0]
    lon = 0.5*squareCorners[2][1] + 0.5*squareCorners[3][1]
    return [lat,lon]
def calc_distance(x1, y1, x2, y2):
    dx = x2 - x1
    dy = y2 - y1
    return math.sqrt(dx*dx + dy*dy)

distLat = rows[1] - rows[0]
distLon = cols[1] - cols[0]
diagDist = math.sqrt(distLat*distLat + distLon*distLon)

for nSquare in range(len(singleBounds)):
    centres.append(getCentreLatLong(singleBounds[nSquare]))
    dist = calc_distance(centres[-1][0],centres[-1][1],ams_center[0],ams_center[1])
    if centres[-1][0] == ams_center[0]:
        distances.append(int(dist*300/distLon))
    elif centres[-1][1] == ams_center[1]:
        distances.append(int(dist*300/distLat))
    else:
        distances.append(round(dist*300*math.sqrt(2)/diagDist,4))
    
print('Total number of centres is: {}'.format(len(centres)))

map_AmsHeart2 = folium.Map(location=ams_center, zoom_start=14)
folium.Marker(ams_center, popup='Dam Square').add_to(map_AmsHeart2)
for innerSquare in range(len(singleBounds)):
    folium.features.RectangleMarker(bounds=singleBounds[innerSquare], color='#a11e06', fill_color='#a11e06', 
                                    fill_opacity=0.2).add_to(map_AmsHeart2)
    folium.CircleMarker(centres[innerSquare], radius=2, color='blue', fill = True, fill_color='blue', 
                                    fill_opacity=0.2).add_to(map_AmsHeart2)
    
    # print("Square n#{}: centre coordinates: {}, distance: ~{} m".format(innerSquare, centres[innerSquare],distances[innerSquare]))

map_AmsHeart2

Total number of centres is: 81


Now that all the coordinates of the neighborhoods/areas centers have been identified, let's use the python **geopy geocoder** to get approximate addresses of those locations.

In [11]:
geolocator = Nominatim(user_agent="foursquare_agent")
addresses = []
print('Obtaining location addresses: ', end='')
for coord in centres:
    loc = geolocator.reverse(coord)
    addresses.append(loc.address.split(', Noord-Holland')[0])
    print(' .', end='')
print(' done.')

Obtaining location addresses:  . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . done.


In [12]:
addresses[:10]

['124, Vondelstraat, Vondelbuurt, Amsterdam',
 'Helmersbuurt, Amsterdam',
 '53-3, Kinkerstraat, Oud-West, Amsterdam',
 '11-1, Allard Piersonstraat, Da Costabuurt, Amsterdam',
 'De Poort, 18, Hugo de Grootkade, Frederik Hendrikbuurt, Amsterdam',
 '33-H, Eerste Hugo de Grootstraat, Frederik Hendrikbuurt, Amsterdam',
 '228, Van der Palmkade, Staatsliedenbuurt, Amsterdam',
 '79-H, Groen van Prinstererstraat, Staatsliedenbuurt, Amsterdam',
 '141-H, Haarlemmerweg, Amsterdam',
 '17, Roemer Visscherstraat, Vondelbuurt, Amsterdam']

Let's now place all the addresses into a Pandas dataframe.

In [13]:
latitudes = [item[0] for item in centres]
longitudes = [item[1] for item in centres]
df_locations = pd.DataFrame({'Address': addresses,
                             'Latitude': latitudes,
                             'Longitude': longitudes,
                             'Distance from centre (m)': distances})

df_locations.head(10)

Address   Latitude  Longitude  \
0          124, Vondelstraat, Vondelbuurt, Amsterdam  52.361261   4.872937   
1                            Helmersbuurt, Amsterdam  52.364256   4.872937   
2            53-3, Kinkerstraat, Oud-West, Amsterdam  52.367252   4.872937   
3  11-1, Allard Piersonstraat, Da Costabuurt, Ams...  52.370248   4.872937   
4  De Poort, 18, Hugo de Grootkade, Frederik Hend...  52.373243   4.872937   
5  33-H, Eerste Hugo de Grootstraat, Frederik Hen...  52.376239   4.872937   
6  228, Van der Palmkade, Staatsliedenbuurt, Amst...  52.379234   4.872937   
7  79-H, Groen van Prinstererstraat, Staatslieden...  52.382230   4.872937   
8                    141-H, Haarlemmerweg, Amsterdam  52.385226   4.872937   
9  17, Roemer Visscherstraat, Vondelbuurt, Amsterdam  52.361261   4.877832   

   Distance from centre (m)  
0                 1697.0569  
1                 1592.6799  
2                 1513.7249  
3                 1464.3098  
4                 1447.4631  
5                 1464.3094  
6                 1513.7242  
7                 1592.6790  
8                 1697.0557  
9                 1401.2045

### Foursquare API
Now that all the location candidates are set, let's use Foursquare API to get info on food locations, universities and parks in each neighborhood.

The interest is in venues in 'food' category, but only those that are not real restaurants, as the new location will be a take away.
However, as it will be an *italian* take away, Italian restaurants will be included in the search.
In addition, the search will include parks, universities and offices within the defined neighborhoods. 

In [14]:
# =============================================================================
# Foursquare Credentials
# =============================================================================

# FOURSQUARE CREDENTIALS HIDDEN FOR SHARING

In [15]:
# =============================================================================
# Category IDs corresponding to Italian restaurants, offices, parks and university 
# were taken from Foursquare web site (https://developer.foursquare.com/docs/resources/categories):
# =============================================================================
food_category = '4d4b7105d754a06374d81259'         # 'Root' category for all food-related venues
uni_category = '4d4b7105d754a06372d81259'          # 'Root' category for all college-related venues
park_category = '4d4b7105d754a06377d81259'         # 'Root' category for Outdoors & Recreation venues
professional_category = '4d4b7105d754a06375d81259' # 'Root' category for Professional & Other Places
#professional_category = ['4d4b7105d754a06378d81259']
# =============================================================================
# Listing all interesting IDs for each unique category
# =============================================================================
italian_restaurant_categories = ['4bf58dd8d48988d110941735']
university_categories = ['4bf58dd8d48988d1ae941735','4bf58dd8d48988d1ab941735'] # university and student center
parks_categories = ['4bf58dd8d48988d163941735','52e81612bcbc57f1066b7a25'] # park and pedestrian plaza
businessCenter_categories = ['56aa371be4b08b9a8d573517','4bf58dd8d48988d124941735'] # busieness centre and office
#businessCenter_categories = ['5453de49498eade8af355881']

def isNot_restaurant(categories, specific_filter=None):
    restaurant_words = ['restaurant', 'diner', 'taverna', 'steakhouse']
    restaurant = False
    specific = False
    for c in categories:
        category_name = c[0].lower()
        category_id = c[1]
        for r in restaurant_words:
            if r in category_name:
                restaurant = False
        if 'fast food' in category_name:
            restaurant = True
        if not(specific_filter is None) and (category_id in specific_filter):
            specific = True
            restaurant = True
    return restaurant, specific

def is_openAir(categories, specific_filter=None):
    openAir = False
    specific = False
    for c in categories:
        category_name = c[0].lower()
        category_id = c[1]
        if not(specific_filter is None) and (category_id in specific_filter):
            specific = True
            openAir = True
    return openAir, specific

def is_Univ(categories, specific_filter=None):
    college = False
    specific = False
    for c in categories:
        category_name = c[0].lower()
        category_id = c[1]
        if not(specific_filter is None) and (category_id in specific_filter):
            specific = True
            college = True
    return college, specific

def is_busin(categories, specific_filter=None):
    service = False
    specific = False
    for c in categories:
        category_name = c[0].lower()
        category_id = c[1]
        if not(specific_filter is None) and (category_id in specific_filter):
            specific = True
            service = True
    return service, specific

def get_categories(categories):
    return [(cat['name'], cat['id']) for cat in categories]

def format_address(location):
    address = ', '.join(location['formattedAddress'])
    address = address.split(', Nederland')[0]
    address = address.replace(', Noord-Holland', '')
    return address

def get_venues_near_location(lat, lon, category, client_id, client_secret, radius=500, limit=100):
    version = '20180724'
    url = 'https://api.foursquare.com/v2/venues/explore?client_id={}&client_secret={}&v={}&ll={},{}&categoryId={}&radius={}&limit={}'.format(
        client_id, client_secret, version, lat, lon, category, radius, limit)
    try:
        results = requests.get(url).json()['response']['groups'][0]['items']
        venues = [(item['venue']['id'],
                   item['venue']['name'],
                   get_categories(item['venue']['categories']),
                   (item['venue']['location']['lat'], item['venue']['location']['lng']),
                   format_address(item['venue']['location']),
                   item['venue']['location']['distance']) for item in results]        
    except:
        venues = []
    return venues

In [16]:
# Let's now go over our neighborhood locations and get nearby food places, parks, universities and offices;
# A dictionary of all found venues will be maintained

def get_NotRestaurants(lats, lons):
    notRestaurants = {}
    italian_restaurants = {}
    location_restaurants = []

    print('Obtaining fast food and italian restaurants around candidate locations:', end='')
    for lat, lon in zip(lats, lons):
        # Using radius=300 to meke sure we have overlaps/full coverage so we don't miss any restaurant (we're using dictionaries to remove any duplicates resulting from area overlaps)
        venues = get_venues_near_location(lat, lon, food_category, foursquare_client_id, foursquare_client_secret, radius=300, limit=100)
        area_restaurants = []
        for venue in venues:
            venue_id = venue[0]
            venue_name = venue[1]
            venue_categories = venue[2]
            venue_latlon = venue[3]
            venue_address = venue[4]
            venue_distance = venue[5]
            is_notRes, is_italian = isNot_restaurant(venue_categories, specific_filter=italian_restaurant_categories)
            if is_notRes:
                #x, y = lonlat_to_xy(venue_latlon[1], venue_latlon[0])
                restaurant = (venue_id, venue_name, venue_latlon[0], venue_latlon[1], venue_address, venue_distance, is_italian)
                if venue_distance<=300:
                    area_restaurants.append(restaurant)
                notRestaurants[venue_id] = restaurant
                if is_italian:
                    italian_restaurants[venue_id] = restaurant
        location_restaurants.append(area_restaurants)
        print(' .', end='')
    print(' done.')
    return notRestaurants, italian_restaurants, location_restaurants

def get_parks(lats, lons):
    parkArea = {}
    location_parks = []

    print('Obtaining green areas around candidate locations:', end='')
    for lat, lon in zip(lats, lons):
        venues = get_venues_near_location(lat, lon, park_category, foursquare_client_id, foursquare_client_secret, radius=300, limit=100)
        area_parks = []
        for venue in venues:
            venue_id = venue[0]
            venue_name = venue[1]
            venue_categories = venue[2]
            venue_latlon = venue[3]
            venue_address = venue[4]
            venue_distance = venue[5]
            is_Outdoor, is_Park = is_openAir(venue_categories, specific_filter=parks_categories)
            if is_Park:
                #x, y = lonlat_to_xy(venue_latlon[1], venue_latlon[0])
                park = (venue_id, venue_name, venue_categories, venue_latlon[0], venue_latlon[1], venue_address, venue_distance)
                if venue_distance<=300:
                    area_parks.append(park)
                parkArea[venue_id] = area_parks
        location_parks.append(area_parks)
        print(' .', end='')
    print(' done.')
    return parkArea, location_parks

def get_uni(lats, lons):
    universityArea = {}
    location_uni = []

    print('Obtaining university venues around candidate locations:', end='')
    for lat, lon in zip(lats, lons):
        venues = get_venues_near_location(lat, lon, uni_category, foursquare_client_id, foursquare_client_secret, radius=300, limit=100)
        area_uni = []
        for venue in venues:
            venue_id = venue[0]
            venue_name = venue[1]
            venue_categories = venue[2]
            venue_latlon = venue[3]
            venue_address = venue[4]
            venue_distance = venue[5]
            is_College, is_Uni = is_Univ(venue_categories, specific_filter=university_categories)
            if is_Uni:
                university = (venue_id, venue_name, venue_latlon[0], venue_latlon[1], venue_address, venue_distance)
                if venue_distance<=300:
                    area_uni.append(university)
                universityArea[venue_id] = area_uni
        location_uni.append(area_uni)
        print(' .', end='')
    print(' done.')
    return universityArea, location_uni

def get_businessOffices(lats, lons):
    officeArea = {}
    location_offices = []

    print('Obtaining office venues around candidate locations:', end='')
    for lat, lon in zip(lats, lons):
        venues = get_venues_near_location(lat, lon, professional_category, foursquare_client_id, foursquare_client_secret, radius=300, limit=100)
        area_office = []
        for venue in venues:
            venue_id = venue[0]
            venue_name = venue[1]
            venue_categories = venue[2]
            venue_latlon = venue[3]
            venue_address = venue[4]
            venue_distance = venue[5]
            is_Professional, is_Office = is_busin(venue_categories, specific_filter=businessCenter_categories)
            if is_Office:
                office = (venue_id, venue_name, venue_latlon[0], venue_latlon[1], venue_address, venue_distance)
                if venue_distance<=300:
                    area_office.append(office)
                officeArea[venue_id] = area_office
        location_offices.append(area_office)
        print(' .', end='')
    print(' done.')
    return officeArea, location_offices


In [17]:
# =============================================================================
# Try to load from local file system in case we did this before
# =============================================================================
import pickle

notRestaurants = {}
italian_restaurants = {}
location_restaurants = []
notRest_loaded = False
try:
    with open('restaurants.pkl', 'rb') as f:
        notRestaurants = pickle.load(f)
    with open('italian_restaurants.pkl', 'rb') as f:
        italian_restaurants = pickle.load(f)
    with open('location_restaurants.pkl', 'rb') as f:
        location_restaurants = pickle.load(f)
    print('Restaurant data loaded.')
    notRest_loaded = True
except:
    pass

if not notRest_loaded:
    notRestaurants, italian_restaurants, location_restaurants = get_NotRestaurants(latitudes, longitudes)

    with open('restaurants.pkl', 'wb') as f:
        pickle.dump(notRestaurants, f)
    with open('italian_restaurants.pkl', 'wb') as f:
        pickle.dump(italian_restaurants, f)
    with open('location_restaurants.pkl', 'wb') as f:
        pickle.dump(location_restaurants, f)
# =============================================================================
parkArea = {}
location_parks = []
park_loaded = False
try:
    with open('parks.pkl', 'rb') as f:
        parkArea = pickle.load(f)
    with open('location_parks.pkl', 'rb') as f:
        location_parks = pickle.load(f)
    print('Green Areas data loaded.')
    park_loaded = True
except:
    pass

if not park_loaded:
    parkArea, location_parks = get_parks(latitudes, longitudes)

    with open('parks.pkl', 'wb') as f:
        pickle.dump(parkArea, f)
    with open('location_parks.pkl', 'wb') as f:
        pickle.dump(location_parks, f)
# =============================================================================
universityArea = {}
location_uni = []
uni_loaded = False
try:
    with open('uni.pkl', 'rb') as f:
        universityArea = pickle.load(f)
    with open('location_uni.pkl', 'rb') as f:
        location_uni = pickle.load(f)
    print('Universities data loaded.')
    uni_loaded = True
except:
    pass

if not uni_loaded:
    universityArea, location_uni = get_uni(latitudes, longitudes)
    
    with open('uni.pkl', 'wb') as f:
        pickle.dump(universityArea, f)
    with open('location_uni.pkl', 'wb') as f:
        pickle.dump(location_uni, f)
# =============================================================================
officeArea = {}
location_offices = []
office_loaded = False
try:
    with open('office.pkl', 'rb') as f:
        officeArea = pickle.load(f)
    with open('location_office.pkl', 'rb') as f:
        location_offices = pickle.load(f)
    print('Offices data loaded.')
    office_loaded = True
except:
    pass

if not office_loaded:
    officeArea, location_offices = get_businessOffices(latitudes, longitudes)

    with open('office.pkl', 'wb') as f:
        pickle.dump(officeArea, f)
    with open('location_office.pkl', 'wb') as f:
        pickle.dump(location_offices, f)


Restaurant data loaded.
Green Areas data loaded.
Universities data loaded.
Offices data loaded.


In [18]:
# =============================================================================
# Printing some global results
# =============================================================================
print('Total number of food places:', len(notRestaurants))
print('Total number of Italian restaurants:', len(italian_restaurants))
print('Percentage of Italian restaurants: {:.2f}%'.format(len(italian_restaurants) / len(notRestaurants) * 100))
print('Average number of restaurants in neighborhood:', numpy.array([len(r) for r in location_restaurants]).mean())
print('---')
print('Total number of green areas:', len(parkArea))
print('Average number of green areas in neighborhood:', numpy.array([len(r) for r in location_parks]).mean())
print('---')
print('Total number of universities:', len(universityArea))
print('Average number of universities in neighborhood:', numpy.array([len(r) for r in location_uni]).mean())
print('---')
print('Total number of offices:', len(officeArea))
print('Average number of offices in neighborhood:', numpy.array([len(r) for r in location_offices]).mean())

Total number of food places: 93
Total number of Italian restaurants: 87
Percentage of Italian restaurants: 93.55%
Average number of restaurants in neighborhood: 2.567901234567901
---
Total number of green areas: 22
Average number of green areas in neighborhood: 0.5925925925925926
---
Total number of universities: 35
Average number of universities in neighborhood: 0.8888888888888888
---
Total number of offices: 379
Average number of offices in neighborhood: 10.592592592592593


Let's now see all the collected venues in the area of interest on a folium map. Each venue is displayed with a circle marker and its category can be recognized using the following color legend:
* red: italian restaurant
* blue: fast food
* green: parks
* orange: universities
* violet: offices

In [19]:
map_AmsHeart = folium.Map(location=ams_center, zoom_start=14)
folium.Marker(ams_center, popup='Dam Square').add_to(map_AmsHeart)
for res in notRestaurants.values():
    lat = res[2]; lon = res[3]
    is_italian = res[6]
    color = 'red' if is_italian else 'blue'
    folium.CircleMarker([lat, lon], radius=2.5, color=color, fill=True, fill_color=color, fill_opacity=1).add_to(map_AmsHeart)
for park in parkArea.values():
    lat = park[0][3]; lon = park[0][4]
    color = 'green'
    folium.CircleMarker([lat, lon], radius=2.5, color=color, fill=True, fill_color=color, fill_opacity=1).add_to(map_AmsHeart)
for uni in universityArea.values():
    lat = uni[0][2]; lon = uni[0][3]
    color = 'orange'
    folium.CircleMarker([lat, lon], radius=2.5, color=color, fill=True, fill_color=color, fill_opacity=1).add_to(map_AmsHeart)
for office in officeArea.values():
    lat = office[0][2]; lon = office[0][3]
    color = 'DarkViolet'
    folium.CircleMarker([lat, lon], radius=2.5, color=color, fill=True, fill_color=color, fill_opacity=1).add_to(map_AmsHeart)
    
map_AmsHeart

The acquisition of all venues of interest that are in the area within few kilometers from Dam Square, concludes the data gathering phase.
This data will be next used to find the optimal location for the italian take away.

<a id="methodology"></a>
## 3. Methodology

In the next section, instruments given by exploratory data analysis will be used to analyze the collected data.
In particular, efforts will be directed on detecting areas of Amsterdam centre that have low italian restaurants density and are close to green areas, universities and offices at the same time. 

The analysis will be limited to an area of ~3x3km around city center.

In the first step all the required data have been collected. Second step will be the calculation and exploration of italian restaurants density, parks, universities and offices density across different areas of Amsterdam. Heatmaps will be used to identify a few promising areas close to the center with low number of italian restaurants and high density of university, parks and offices. The attention will then be focused on those areas.

In a third and final step the attention will be on the most promising areas. Locations with no more than three restaurants in radius of 200 metres and at least two venues among Parks, Universities and offices in radius of 200 metres will be taken into account. Within those, clusters of locations that meet some basic requirements established in discussion with stakeholders will be created.
Finally, general zones, neighborhoods and addresses of final candidate location will be listed, which should be a starting point for final 'street level' exploration and search for optimal venue location by stakeholders.


<a id="analysis"></a>
## 4. Analysis

Performing some basic explanatory data analysis and deriving additional info from the gathered raw data. First, let's count the **number of italian restaurants and fast food in every area candidate**:

In [20]:
loc_restaurants_count = [len(res) for res in location_restaurants]
df_locations['Restaurants in area'] = loc_restaurants_count

print('Average number of restaurants in every area with side=300m:', numpy.array(loc_restaurants_count).mean())
df_locations.head(10)

Average number of restaurants in every area with side=300m: 2.567901234567901


Address   Latitude  Longitude  \
0          124, Vondelstraat, Vondelbuurt, Amsterdam  52.361261   4.872937   
1                            Helmersbuurt, Amsterdam  52.364256   4.872937   
2            53-3, Kinkerstraat, Oud-West, Amsterdam  52.367252   4.872937   
3  11-1, Allard Piersonstraat, Da Costabuurt, Ams...  52.370248   4.872937   
4  De Poort, 18, Hugo de Grootkade, Frederik Hend...  52.373243   4.872937   
5  33-H, Eerste Hugo de Grootstraat, Frederik Hen...  52.376239   4.872937   
6  228, Van der Palmkade, Staatsliedenbuurt, Amst...  52.379234   4.872937   
7  79-H, Groen van Prinstererstraat, Staatslieden...  52.382230   4.872937   
8                    141-H, Haarlemmerweg, Amsterdam  52.385226   4.872937   
9  17, Roemer Visscherstraat, Vondelbuurt, Amsterdam  52.361261   4.877832   

   Distance from centre (m)  Restaurants in area  
0                 1697.0569                    0  
1                 1592.6799                    1  
2                 1513.7249                    2  
3                 1464.3098                    3  
4                 1447.4631                    1  
5                 1464.3094                    2  
6                 1513.7242                    2  
7                 1592.6790                    6  
8                 1697.0557                    5  
9                 1401.2045                    0

Let's repeat the same for **parks, universities and offices**:

In [21]:
loc_parks_count = [len(par) for par in location_parks]
df_locations['Parks in area'] = loc_parks_count

loc_uni_count = [len(uni) for uni in location_uni]
df_locations['Universities in area'] = loc_uni_count

loc_offic_count = [len(off) for off in location_offices]
df_locations['Offices in area'] = loc_offic_count

print('Average number of parks in every area with side=300m:', numpy.array(loc_parks_count).mean())
print('Average number of universities in every area with side=300m:', numpy.array(loc_uni_count).mean())
print('Average number of offices in every area with side=300m:', numpy.array(loc_offic_count).mean())
df_locations.head(10)

Average number of parks in every area with side=300m: 0.5925925925925926
Average number of universities in every area with side=300m: 0.8888888888888888
Average number of offices in every area with side=300m: 10.592592592592593


Address   Latitude  Longitude  \
0          124, Vondelstraat, Vondelbuurt, Amsterdam  52.361261   4.872937   
1                            Helmersbuurt, Amsterdam  52.364256   4.872937   
2            53-3, Kinkerstraat, Oud-West, Amsterdam  52.367252   4.872937   
3  11-1, Allard Piersonstraat, Da Costabuurt, Ams...  52.370248   4.872937   
4  De Poort, 18, Hugo de Grootkade, Frederik Hend...  52.373243   4.872937   
5  33-H, Eerste Hugo de Grootstraat, Frederik Hen...  52.376239   4.872937   
6  228, Van der Palmkade, Staatsliedenbuurt, Amst...  52.379234   4.872937   
7  79-H, Groen van Prinstererstraat, Staatslieden...  52.382230   4.872937   
8                    141-H, Haarlemmerweg, Amsterdam  52.385226   4.872937   
9  17, Roemer Visscherstraat, Vondelbuurt, Amsterdam  52.361261   4.877832   

   Distance from centre (m)  Restaurants in area  Parks in area  \
0                 1697.0569                    0              0   
1                 1592.6799                    1              0   
2                 1513.7249                    2              0   
3                 1464.3098                    3              1   
4                 1447.4631                    1              2   
5                 1464.3094                    2              3   
6                 1513.7242                    2              2   
7                 1592.6790                    6              0   
8                 1697.0557                    5              1   
9                 1401.2045                    0              1   

   Universities in area  Offices in area  
0                     1                5  
1                     0                4  
2                     0                1  
3                     0                3  
4                     1                3  
5                     2                5  
6                     1                3  
7                     0                2  
8                     1                9  
9                     0               10

Let's now calculate the **distance to nearest Italian restaurant from every area candidate center** (not only those within 300m - we want distance to closest one, regardless of how distant it is). The same will be repeated for **parks, universities and offices**.

In [22]:
distances_to_italian_restaurant = []
distances_to_parks = []
distances_to_uni = []
distances_to_offices= []

def getDistanceRest(venueType):
    for area_lat, area_lon in zip(latitudes, longitudes):
        min_distance = 10000
        for res in venueType:
            venue_lat = res[2]
            venue_lon = res[3]
            dist = calc_distance(area_lat, area_lon, venue_lat, venue_lon)
            d = round(dist*300*math.sqrt(2)/diagDist,4)
            if d<min_distance:
                min_distance = d
        distances_to_italian_restaurant.append(min_distance)
    return distances_to_italian_restaurant

def getDistanceUni(venueType):
    for area_lat, area_lon in zip(latitudes, longitudes):
        min_distance = 10000
        for uni in venueType:
            venue_lat = uni[0][2]
            venue_lon = uni[0][3]
            dist = calc_distance(area_lat, area_lon, venue_lat, venue_lon)
            d = round(dist*300*math.sqrt(2)/diagDist,4)
            if d<min_distance:
                min_distance = d
        distances_to_uni.append(min_distance)
    return distances_to_uni

def getDistancePark(venueType):
    for area_lat, area_lon in zip(latitudes, longitudes):
        min_distance = 10000
        for park in venueType:
            venue_lat = park[0][3]
            venue_lon = park[0][4]
            dist = calc_distance(area_lat, area_lon, venue_lat, venue_lon)
            d = round(dist*300*math.sqrt(2)/diagDist,4)
            if d<min_distance:
                min_distance = d
        distances_to_parks.append(min_distance)
    return distances_to_parks

def getDistanceOffices(venueType):
    for area_lat, area_lon in zip(latitudes, longitudes):
        min_distance = 10000
        for off in venueType:
            venue_lat = off[0][2]
            venue_lon = off[0][3]
            dist = calc_distance(area_lat, area_lon, venue_lat, venue_lon)
            d = round(dist*300*math.sqrt(2)/diagDist,4)
            if d<min_distance:
                min_distance = d
        distances_to_offices.append(min_distance)
    return distances_to_offices

df_locations['Distance to Italian restaurant'] = getDistanceRest(italian_restaurants.values())
df_locations['Distance to universities'] = getDistanceUni(universityArea.values())
df_locations['Distance to parks'] = getDistancePark(parkArea.values())
df_locations['Distance to offices'] = getDistanceOffices(officeArea.values())

df_locations.head(10)

Address   Latitude  Longitude  \
0          124, Vondelstraat, Vondelbuurt, Amsterdam  52.361261   4.872937   
1                            Helmersbuurt, Amsterdam  52.364256   4.872937   
2            53-3, Kinkerstraat, Oud-West, Amsterdam  52.367252   4.872937   
3  11-1, Allard Piersonstraat, Da Costabuurt, Ams...  52.370248   4.872937   
4  De Poort, 18, Hugo de Grootkade, Frederik Hend...  52.373243   4.872937   
5  33-H, Eerste Hugo de Grootstraat, Frederik Hen...  52.376239   4.872937   
6  228, Van der Palmkade, Staatsliedenbuurt, Amst...  52.379234   4.872937   
7  79-H, Groen van Prinstererstraat, Staatslieden...  52.382230   4.872937   
8                    141-H, Haarlemmerweg, Amsterdam  52.385226   4.872937   
9  17, Roemer Visscherstraat, Vondelbuurt, Amsterdam  52.361261   4.877832   

   Distance from centre (m)  Restaurants in area  Parks in area  \
0                 1697.0569                    0              0   
1                 1592.6799                    1              0   
2                 1513.7249                    2              0   
3                 1464.3098                    3              1   
4                 1447.4631                    1              2   
5                 1464.3094                    2              3   
6                 1513.7242                    2              2   
7                 1592.6790                    6              0   
8                 1697.0557                    5              1   
9                 1401.2045                    0              1   

   Universities in area  Offices in area  Distance to Italian restaurant  \
0                     1                5                        211.9465   
1                     0                4                        245.7676   
2                     0                1                        280.9397   
3                     0                3                        114.0842   
4                     1                3                        125.2630   
5                     2                5                        232.9967   
6                     1                3                         86.0326   
7                     0                2                        141.4246   
8                     1                9                         58.7600   
9                     0               10                        180.6070   

   Distance to universities  Distance to parks  Distance to offices  
0                  165.0499           583.2698             168.9166  
1                  386.3762           566.0717             145.9762  
2                  607.8141           375.7659             259.5786  
3                  406.3952           213.9512             129.1034  
4                  231.7740           220.1286              23.2327  
5                  148.9331           167.1853             128.0786  
6                  174.7848           154.7782             126.6486  
7                  363.0891           343.6102             167.9922  
8                  196.3155           174.1612              98.7240  
9                  406.1813           253.5164             107.3537

In [23]:
print('Average distance to closest Italian restaurant from each area center:', df_locations['Distance to Italian restaurant'].mean())
print('Average distance to closest university from each area center:', df_locations['Distance to universities'].mean())
print('Average distance to closest park from each area center:', df_locations['Distance to parks'].mean())
print('Average distance to closest office from each area center:', df_locations['Distance to offices'].mean())

Average distance to closest Italian restaurant from each area center: 174.11773950617282
Average distance to closest university from each area center: 344.1558962962963
Average distance to closest park from each area center: 435.27216049382713
Average distance to closest office from each area center: 139.73532345679016


Let's crete a map showing **heatmap / density of restaurants** and try to extract some meaningfull info from that. Also, let's show **borders of Amsterdam boroughs**.

In [24]:
ams_boroughs_url =  'https://maps.amsterdam.nl/open_geodata/geojson.php?KAARTLAAG=GEBIED_BUURTCOMBINATIES&THEMA=gebiedsindeling'
ams_boroughs = requests.get(ams_boroughs_url).json()

def boroughs_style(feature):
    return { 'color': 'blue', 'fill': False }

restaurant_latlons = [[res[2], res[3]] for res in notRestaurants.values()]
italian_latlons = [[res[2], res[3]] for res in italian_restaurants.values()]

In [25]:
from folium import plugins
from folium.plugins import HeatMap
gradientIta = {.33: 'green', .66: 'white', 1: 'red'}
gradientFastFood = {.33: 'blue', .66: 'white', 1: 'pink'}

map_ams = folium.Map(location=ams_center, zoom_start=14)
folium.TileLayer('cartodbpositron').add_to(map_ams) #cartodbpositron cartodbdark_matter
HeatMap(restaurant_latlons, gradient=gradientFastFood).add_to(map_ams)
HeatMap(italian_latlons, gradient=gradientIta).add_to(map_ams)
folium.Marker(ams_center).add_to(map_ams)

folium.GeoJson(ams_boroughs, style_function=boroughs_style, name='geojson').add_to(map_ams)
map_ams

It looks like a few pockets of low italian restaurant and fast food density closest to city center can be found **east and west from Dam Sqaure**. 
Let's crete a map showing **heatmap / density of universities, parks and offices** to see if the above mentioned pockets can be good candidates for an italian take away.

In [26]:
uni_latlons = [[uni[0][2], uni[0][3]] for uni in universityArea.values()]
parks_latlons = [[park[0][3], park[0][4]] for park in parkArea.values()]
offices_latlons = [[off[0][2], off[0][3]] for off in officeArea.values()]


map_ams = folium.Map(location=ams_center, zoom_start=14)
folium.TileLayer('cartodbpositron').add_to(map_ams) #cartodbpositron cartodbdark_matter
HeatMap(uni_latlons).add_to(map_ams)
HeatMap(parks_latlons).add_to(map_ams)
HeatMap(offices_latlons).add_to(map_ams)
folium.Marker(ams_center).add_to(map_ams)

folium.GeoJson(ams_boroughs, style_function=boroughs_style, name='geojson').add_to(map_ams)
map_ams

Graphically comparing the two plots, it is evident that both east and west areas close to Dam Sqare are very good candidates for the italian take away. Based on this, the focus will be on areas *east and west from Dam Square*, that correspond to neighborhoods **Centrum West and Centrum Oost**.

In [27]:
ams_neighb_url = 'https://maps.amsterdam.nl/open_geodata/geojson.php?KAARTLAAG=GEBIED_BUURTEN&THEMA=gebiedsindeling'
ams_neighb = requests.get(ams_neighb_url).json()
map_ams = folium.Map(location=ams_center, zoom_start=15)
folium.TileLayer('cartodbpositron').add_to(map_ams) #cartodbpositron cartodbdark_matter
HeatMap(uni_latlons).add_to(map_ams)
HeatMap(italian_latlons, gradient = gradientIta).add_to(map_ams)
HeatMap(parks_latlons).add_to(map_ams)
HeatMap(offices_latlons).add_to(map_ams)
folium.Marker(ams_center).add_to(map_ams)

folium.GeoJson(ams_neighb, style_function=boroughs_style, name='geojson').add_to(map_ams)
map_ams

![image.jpeg](https://miro.medium.com/max/875/1*zk7RSTn2HdC3htm-hITtKw.jpeg)

Carefully looking at both areas, **Centrum Oost** seems to have a lower italian restaurants density, especially south-west from Prins-Hendrikkade. Let's then define a new, more narrow region of interest, delimited by Prins-Hendrikkade, Dam Square and the Amstel river.
Almost in the middle of this area there's another quite famous square of Amsterdam, called **Nieuwmarkt**. Let's use Nieuwmarkt coordinates to define the centre for this new area.

In [28]:
address = 'Nieuwmarkt, Amsterdam'
ams_Nieuwmarkt = get_coordinates(address)
print('Coordinate of {}: {}'.format(address, ams_Nieuwmarkt))

Coordinate of Nieuwmarkt, Amsterdam: [52.37263245, 4.9003694561530535]


In [29]:
map_ams = folium.Map(location=ams_Nieuwmarkt, zoom_start=16)
folium.TileLayer('cartodbpositron').add_to(map_ams) #cartodbpositron cartodbdark_matter
HeatMap(uni_latlons).add_to(map_ams)
HeatMap(italian_latlons, gradient = gradientIta).add_to(map_ams)
HeatMap(parks_latlons).add_to(map_ams)
HeatMap(offices_latlons).add_to(map_ams)
folium.Marker(ams_Nieuwmarkt, popup='Nieuwmarkt, Amsterdam').add_to(map_ams)
folium.Marker(ams_center, popup='Dam Square, Amsterdam').add_to(map_ams)
folium.GeoJson(ams_neighb, style_function=boroughs_style, name='geojson').add_to(map_ams)
map_ams

Let's identify a region centred in Nieuwmarkt to analyse the number of venues for each selected category that are present in this area.

In [30]:
distKm = 0.5
# BOUNDING BOX COORDINATES

bottomLeft_zoom = [float(geodesic(kilometers=distKm).destination(Point(ams_Nieuwmarkt[0], ams_Nieuwmarkt[1]), 180).format_decimal().split(',')[0]),float(geodesic(kilometers=distKm).destination(Point(ams_Nieuwmarkt[0], ams_Nieuwmarkt[1]), 270).format_decimal().split(',')[1])]
bottomRight_zoom = [float(geodesic(kilometers=distKm).destination(Point(ams_Nieuwmarkt[0], ams_Nieuwmarkt[1]), 180).format_decimal().split(',')[0]),float(geodesic(kilometers=distKm).destination(Point(ams_Nieuwmarkt[0], ams_Nieuwmarkt[1]), 90).format_decimal().split(',')[1])]
topLeft_zoom = [float(geodesic(kilometers=distKm).destination(Point(ams_Nieuwmarkt[0], ams_Nieuwmarkt[1]), 0).format_decimal().split(',')[0]),float(geodesic(kilometers=distKm).destination(Point(ams_Nieuwmarkt[0], ams_Nieuwmarkt[1]), 270).format_decimal().split(',')[1])]
topRight_zoom = [float(geodesic(kilometers=distKm).destination(Point(ams_Nieuwmarkt[0], ams_Nieuwmarkt[1]), 0).format_decimal().split(',')[0]),float(geodesic(kilometers=distKm).destination(Point(ams_Nieuwmarkt[0], ams_Nieuwmarkt[1]), 90).format_decimal().split(',')[1])]
print('Corner Coordinates of the square area around {}: top left corner {} , top right corner {}, bottom left corner {}, bottom right corner {}'.format(address, topLeft_zoom, topRight_zoom, bottomLeft_zoom, bottomRight_zoom))


Corner Coordinates of the square area around Nieuwmarkt, Amsterdam: top left corner [52.37712584389357, 4.893027992820081] , top right corner [52.37712584389357, 4.907710919486026], bottom left corner [52.36813905266996, 4.893027992820081], bottom right corner [52.36813905266996, 4.907710919486026]


In [31]:
nOfDivisions_zoom = int(1000/200)
cols_zoom = numpy.linspace(bottomLeft_zoom[1], bottomRight_zoom[1], num=nOfDivisions_zoom)
rows_zoom = numpy.linspace(bottomLeft_zoom[0], topLeft_zoom[0], num=nOfDivisions_zoom)

print('Number of divisions is {} so the total number of neighborhoods should be: {}'.format(nOfDivisions_zoom-1, numpy.power(nOfDivisions_zoom-1,2)))

Number of divisions is 4 so the total number of neighborhoods should be: 16


In [32]:
lat_zoom, lon_zoom = numpy.meshgrid(rows_zoom, cols_zoom)
singleBounds_zoom = []
for s1 in range(1,len(lon_zoom)):
    for s2 in range(1,len(lon_zoom[s1])):
        localBounds = [[lat_zoom[s1][s2],lon_zoom[s1][s2]],[lat_zoom[s1-1][s2],lon_zoom[s1-1][s2]],
                       [lat_zoom[s1][s2-1],lon_zoom[s1-1][s2]],[lat_zoom[s1-1][s2-1],lon_zoom[s1][s2]]]
        singleBounds_zoom.append(localBounds)

# CHECKING THE TOTAL NUMBER OF SQUARES (NEIGHBORHOODS)
print('Total number of squares composing the final grid: {}'.format(len(singleBounds_zoom)))

Total number of squares composing the final grid: 16


In [33]:
distLat_zoom = rows_zoom[1] - rows_zoom[0]
distLon_zoom = cols_zoom[1] - cols_zoom[0]
diagDist_zoom = math.sqrt(distLat_zoom*distLat_zoom + distLon_zoom*distLon_zoom)
distances_zoom = []
centres_zoom = []
for nSquare in range(len(singleBounds_zoom)):
    centres_zoom.append(getCentreLatLong(singleBounds_zoom[nSquare]))
    dist = calc_distance(centres_zoom[-1][0],centres_zoom[-1][1],ams_Nieuwmarkt[0],ams_Nieuwmarkt[1])
    if centres_zoom[-1][0] == ams_Nieuwmarkt[0]:
        distances_zoom.append(int(dist*300/distLon_zoom))
    elif centres_zoom[-1][1] == ams_Nieuwmarkt[1]:
        distances_zoom.append(int(dist*300/distLat_zoom))
    else:
        distances_zoom.append(round(dist*300*math.sqrt(2)/diagDist_zoom,4))
    
print(len(centres_zoom), 'candidate neighborhood centers generated.')

map_AmsZoom = folium.Map(location=ams_Nieuwmarkt, zoom_start=16)
folium.Marker(ams_Nieuwmarkt, popup='Nieuwmarkt').add_to(map_AmsZoom)
for innerSquare in range(len(singleBounds_zoom)):
    folium.features.RectangleMarker(bounds=singleBounds_zoom[innerSquare], color='#a11e06', fill_color='#a11e06', 
                                    fill_opacity=0.2).add_to(map_AmsZoom)
    folium.CircleMarker(centres_zoom[innerSquare], radius=4, color='blue', fill = True, fill_color='blue', 
                                    fill_opacity=0.2).add_to(map_AmsZoom)
map_AmsZoom

16 candidate neighborhood centers generated.


OK. Now let's calculate two most important things for each location candidate: **number of food venues in vicinity** (we'll use radius of **250 meters**) and **distances to closest Italian restaurant, university, park and office**.

In [34]:
latitudes_zoom = [item[0] for item in centres_zoom]
longitudes_zoom = [item[1] for item in centres_zoom]

In [35]:
ita_distance = []
ita_count = []
parks_distance = []
parks_count = []
uni_distance = []
uni_count = []
office_distance = []
office_count = []

def count_venues_nearby(venueValues, isRest, isPark, isUni, radius=250):    
    for x, y in zip(latitudes_zoom, longitudes_zoom):
        count = 0
        for res in venueValues:
            if isRest:
                res_x = res[2]; res_y = res[3]
            elif isPark:
                res_x = res[0][3]; res_y = res[0][4]
            else:
                res_x = res[0][2]; res_y = res[0][3]
            dist = calc_distance(x, y, res_x, res_y)
            d = round(dist*300*math.sqrt(2)/diagDist_zoom,4)
            if d<=radius:
                count += 1
        if isRest:
            ita_count.append(count)
        elif isPark:
            parks_count.append(count)
        elif isUni:
            uni_count.append(count)
        else:
            office_count.append(count)

def findNearest(venueType,isRest,isPark,isUni):
    for area_lat, area_lon in zip(latitudes_zoom, longitudes_zoom):
        min_distance = 10000
        for res in venueType:
            if isRest:
                res_x = res[2]; res_y = res[3]
            elif isPark:
                res_x = res[0][3]; res_y = res[0][4]
            else:
                res_x = res[0][2]; res_y = res[0][3]
            dist = calc_distance(area_lat, area_lon, res_x, res_y)
            d = round(dist*300*math.sqrt(2)/diagDist_zoom,4)
            if d<min_distance:
                min_distance = d
        if isRest:
            ita_distance.append(min_distance)
        elif isPark:
            parks_distance.append(min_distance)
        elif isUni:
            uni_distance.append(min_distance)
        else:
            office_distance.append(min_distance)


# Let's put this into dataframe
df_zoom_locations = pd.DataFrame({'Latitude':latitudes_zoom,
                                 'Longitude':longitudes_zoom})

venuesList = [italian_restaurants,parkArea,universityArea,officeArea]
switch = [[True,False,False,False],[False,True,False,False],[False,False,True,False],[False,False,False,True]]

print('Generating data on location candidates... ', end='')
for location in range(len(venuesList)):
    count = count_venues_nearby(venuesList[location].values(), switch[location][0],switch[location][1],
                                switch[location][2], radius=250)
    distance = findNearest(venuesList[location].values(), switch[location][0],switch[location][1],
                                switch[location][2])
print('done.')

df_zoom_locations['Distance to Italian restaurant'] = ita_distance
df_zoom_locations['Italian Restaurants nearby'] = ita_count
df_zoom_locations['Universities nearby'] = uni_count
df_zoom_locations['Parks nearby'] = parks_count
df_zoom_locations['Offices nearby'] = office_count

df_zoom_locations

Generating data on location candidates... done.


Latitude  Longitude  Distance to Italian restaurant  \
0   52.369262   4.894863                        236.9795   
1   52.371509   4.894863                        254.9652   
2   52.373756   4.894863                        175.8758   
3   52.376002   4.894863                         89.4272   
4   52.369262   4.898534                        112.4569   
5   52.371509   4.898534                         50.6084   
6   52.373756   4.898534                        166.3877   
7   52.376002   4.898534                         62.8808   
8   52.369262   4.902205                        335.4052   
9   52.371509   4.902205                        301.2514   
10  52.373756   4.902205                        408.7989   
11  52.376002   4.902205                        392.2411   
12  52.369262   4.905876                        580.4004   
13  52.371509   4.905876                        471.7030   
14  52.373756   4.905876                        297.7162   
15  52.376002   4.905876                        229.9443   

    Italian Restaurants nearby  Universities nearby  Parks nearby  \
0                            1                    4             1   
1                            0                    4             1   
2                            1                    0             0   
3                            6                    0             0   
4                            4                    5             0   
5                            3                    1             0   
6                            1                    0             0   
7                            2                    0             0   
8                            0                    0             0   
9                            0                    0             0   
10                           0                    0             0   
11                           0                    0             0   
12                           0                    0             0   
13                           0                    0             0   
14                           0                    0             0   
15                           1                    0             0   

    Offices nearby  
0                0  
1                0  
2               17  
3               27  
4               10  
5               19  
6                2  
7                2  
8                0  
9                9  
10               0  
11               0  
12              14  
13              10  
14               2  
15               5

Let's now **filter** those locations: we're interested only in **locations with no more than two restaurants in radius of 200 meters**, and **at least two venues among Parks, Universities and offices in radius of 200 metres**.

In [36]:
good_res_count = numpy.array((df_zoom_locations['Italian Restaurants nearby']<=3))
print('Locations with no more than two italian restaurants nearby:', good_res_count.sum())

good_park_count = numpy.array((df_zoom_locations['Parks nearby']>=1))
print('Locations with more than one park nearby:', good_park_count.sum())
good_uni_count = numpy.array((df_zoom_locations['Universities nearby']>=1))
print('Locations with more than one university nearby:', good_uni_count.sum())
good_offices_count = numpy.array((df_zoom_locations['Offices nearby']>=1))
print('Locations with more than one office nearby:', good_offices_count.sum())

good_locations = numpy.logical_and(good_res_count, 
                                   numpy.logical_or(numpy.logical_and(good_park_count,good_uni_count),
                                                    numpy.logical_or(numpy.logical_and(good_park_count,good_offices_count),
                                                                     numpy.logical_and(good_uni_count,good_offices_count))))
print('Locations with both conditions met:', good_locations.sum())

df_good_locations = df_zoom_locations[good_locations]

Locations with no more than two italian restaurants nearby: 14
Locations with more than one park nearby: 2
Locations with more than one university nearby: 4
Locations with more than one office nearby: 11
Locations with both conditions met: 3


In [37]:
df_good_locations

Latitude  Longitude  Distance to Italian restaurant  \
0  52.369262   4.894863                        236.9795   
1  52.371509   4.894863                        254.9652   
5  52.371509   4.898534                         50.6084   

   Italian Restaurants nearby  Universities nearby  Parks nearby  \
0                           1                    4             1   
1                           0                    4             1   
5                           3                    1             0   

   Offices nearby  
0               0  
1               0  
5              19

In [38]:
good_latitudes = df_good_locations['Latitude'].values
good_longitudes = df_good_locations['Longitude'].values

good_locations = [[lat, lon] for lat, lon in zip(good_latitudes, good_longitudes)]

map_ams= folium.Map(location=ams_Nieuwmarkt, zoom_start=16)
folium.TileLayer('cartodbpositron').add_to(map_ams)
HeatMap(uni_latlons).add_to(map_ams)
HeatMap(italian_latlons, gradient = gradientIta).add_to(map_ams)
HeatMap(parks_latlons).add_to(map_ams)
HeatMap(offices_latlons).add_to(map_ams)
folium.Circle(ams_Nieuwmarkt, radius=550, color='white', fill=True, fill_opacity=0.6).add_to(map_ams)
folium.Marker(ams_Nieuwmarkt, popup='Nieuwmarkt').add_to(map_ams)
for lat, lon in zip(good_latitudes, good_longitudes):
    folium.CircleMarker([lat, lon], radius=3, color='red', fill=True, fill_color='red', fill_opacity=1).add_to(map_ams) 
folium.GeoJson(ams_neighb, style_function=boroughs_style, name='geojson').add_to(map_ams)
map_ams

Project is almost at the end. Let's **cluster** those locations to create **centers of zones containing good locations**. These zones, their centers and addresses will be the final result of the analysis.

In [39]:
from sklearn.cluster import KMeans

number_of_clusters = 2

good_xys = df_good_locations[['Latitude', 'Longitude']].values
kmeans = KMeans(n_clusters=number_of_clusters, random_state=0).fit(good_xys)

cluster_centers = [(cc[0], cc[1]) for cc in kmeans.cluster_centers_]

map_ams = folium.Map(location=ams_Nieuwmarkt, zoom_start=16)
folium.TileLayer('cartodbpositron').add_to(map_ams)
HeatMap(uni_latlons).add_to(map_ams)
HeatMap(italian_latlons, gradient = gradientIta).add_to(map_ams)
HeatMap(parks_latlons).add_to(map_ams)
HeatMap(offices_latlons).add_to(map_ams)

folium.Circle(ams_Nieuwmarkt, radius=550, color='white', fill=True, fill_opacity=0.6).add_to(map_ams)
folium.Marker(ams_Nieuwmarkt, popup='Nieuwmarkt').add_to(map_ams)
for lat, lon in zip(good_latitudes, good_longitudes):
    folium.CircleMarker([lat, lon], radius=2, color='red', fill=True, fill_color='red', fill_opacity=1).add_to(map_ams)
for lat, lon in cluster_centers:
    folium.Circle([lat, lon], radius=200, color='purple', fill=True, fill_opacity=0.25).add_to(map_ams) 
folium.GeoJson(ams_neighb, style_function=boroughs_style, name='geojson').add_to(map_ams)
map_ams

The obtained clusters nicely group the candidate locations and cluster centers are well placed in the middle of the zones 'rich' with location candidates.

Addresses of those cluster centers will be a good starting point for exploring the neighborhoods to find the best possible location based on neighborhood specifics.

Let's **reverse geocode those candidate area centers to get the addresses** which can be presented to stakeholders.

In [40]:
geolocator = Nominatim(user_agent="foursquare_agent")

addresses_end = []
print('==============================================================')
print('Centres of area candidates recommended for further analysis')
print('==============================================================\n')
for coord in cluster_centers:
    loc = geolocator.reverse(coord)
    addresses_end.append(loc.address.split(', Noord-Holland')[0])
    
    dist = calc_distance(ams_center[0], ams_center[1], coord[0], coord[1])
    d = round(dist*300*math.sqrt(2)/diagDist,4)
    
    print('{}{} => {:.1f}km from Dam Square'.format(addresses_end[-1], ' '*(62-len(addresses_end[-1])), d/1000))
    

Centres of area candidates recommended for further analysis

217H, Oudezijds Voorburgwal, Burgwallen-Oude Zijde, Amsterdam  => 0.3km from Dam Square
7, Boerensteeg, Burgwallen-Oude Zijde, Amsterdam               => 0.5km from Dam Square


------------------------------------------

This concludes the analysis.
Two addresses have been identified in the heart of Amsterdam, representing the centres of zones containing **few italian restaurants (less than 3)** and **at least two venues among Parks, Universities and offices in radius of 200 metres**

The good locations found are shown on map with a radius of ~200 meters (violet circles) and are located in the Oude Centrum neighborhood, south and south-est from Dam Square. Their centers/addresses can be considered as a good starting point for exploring area neighborhoods in search for potential locations for the take away.


In [41]:
map_ams = folium.Map(location=ams_Nieuwmarkt, zoom_start=16)
folium.Circle(ams_center, radius=20, color='red', fill=True, fill_color='red', fill_opacity=1).add_to(map_ams)
for lonlat, addr in zip(cluster_centers, addresses_end):
    folium.Marker([lonlat[0], lonlat[1]], popup=addr).add_to(map_ams) 
for lat, lon in zip(good_latitudes, good_longitudes):
    folium.Circle([lat, lon], radius=250, color='#0000ff00', fill=True, fill_color='#0066ff', fill_opacity=0.25).add_to(map_ams)
map_ams

<a id="results"></a>
## 5. Results and Discussion 

The analysis shows that a quite small area located south-east from Dam Square presents a low density of Italian restaurants and a few venues in Parks, Universities and Offices categories nearby. Hence, given the initial considerations, ths area found can be considered as a good place to open an italian take away.

Highest concentration of italian restaurants was detected north and south from Dam Square, whilst parks, universities and offices are evenly distributed around the city centre. Thus, the attention was focussed on east and west areas with respect to Dam Square. In particular, after carefully looking at these areas in detail, the south-east one was selected to further investigate the area, as fewer italian restaurants are located in this area and lots of offices, parks and universities can be found at walking distance.

After having defined this more narrow area of interest (covering approx. 0.5x0.5km south-east from Dam Square) a dense grid of location candidates was first created; those locations were then filtered so that those with more than three restaurants in radius of 200m and those with less that one venue among Parks, Universities and offices in radius of 200 metres were removed.

The location candidates were then clustered to create zones of interest which contain the highest number of location candidates. Addresses of centers of these zones were also generated using reverse geocoding, to be used as markers/starting points for more detailed local analysis based on other factors.

The final result is composed of two small areas located 0.3 and 0.5 km south-east from Dam Square. These areas contains three location where an italian take away could open, based on number of italian restaurants in the neighborhood and number of parks, universities and offices nearby. This, of course, does not imply that those zones are actually optimal locations for a take away. The purpose of this analysis was to only provide info on areas in the heart of Amsterdam not already crowded with italian restaurants but with offices, universities and parks in the vicinity, to allow people to take their food and have their lunch outside. Recommended zones should therefore be considered only as a starting point for more detailed analysis which could eventually result in location which has  no nearby competition.

<a id="conclusions"></a>
## 6. Conclusions 

Purpose of this project was to identify an area in the heart of Amsterdam with few italian restaurants in the vicinity but close to offices, universities and parks, in order to help stakeholders in narrowing down the search for optimal locations for a new Italian take away. The idea of the project was indeed to provide a new way to taste italian food, trying to mix the real italian recipes with a more european way of having lunch.

By calculating italian restaurants density distribution from Foursquare data, general boroughs that justify further analysis were first identified. Then, location in these boroughs that satisfy the aformentioned prerequisites were collected and clustered to create major zones of interest. Finally, the addresses of these areas centres were obtained for future usage as starting point for further exploration by stakeholders.

Final decision on optimal restaurant location will be made by stakeholders based on specific characteristics of neighborhoods and locations in every recommended zone, taking into consideration additional factors.